In [1]:
from dawnplot import *
from dawnfrb import *
from io import BytesIO
import base64
import matplotlib.pyplot as plt
import numpy as np

/home/guutz/radioconda/envs/umap/lib/python3.9/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/guutz/radioconda/envs/umap/lib/python3.9/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/home/guutz/radioconda/envs/umap/lib/python3.9/site-packages/umap/distances.

In [2]:
embeddingFeature = get_frb_info('ts')
pad_len = max([len(x) for x in embeddingFeature])
embeddingFeature = [np.concatenate([x, np.zeros(pad_len-len(x))]) for x in embeddingFeature]
embeddingFeatureFFT = np.fft.rfft(embeddingFeature).real

In [3]:
displayProperties = {
    'tns_name': tns_names,
    'dm': get_frb_info('dm'),
    'width_ms': [i*1000 for i in get_frb_info('width_fitb')],
    'n_subbursts': get_frb_info('n_subbursts'),
    'repeater': [1 if rp != -9999.0 else 0 for rp in get_frb_info('repeater_name')]
}

In [4]:

# generate line graphs for tooltips
tooltip_graphs = []
for y1_data, y2_data in zip(list(embeddingFeature),list(embeddingFeatureFFT)):
    # make img src base64 of plot
    img = BytesIO()
    fig = plt.figure(figsize=(2,1))
    plt.plot(y1_data, color='black', linewidth=0.25)
    plt.plot(y2_data, color='red', linewidth=0.25)
    plt.axis('off')
    plt.xlim(0,512)
    plt.savefig(img, format='png', bbox_inches='tight', pad_inches=0)
    plt.close(fig)
    tooltip_graphs.append('data:image/png;base64,' + base64.b64encode(img.getvalue()).decode())  
    
displayProperties['image'] = tooltip_graphs

tooltips = """
    <div>
        <div>
            <img src='@image' style='float: left; margin: 5px 5px 5px 5px'/>
        </div>
        <div>
            <span style="font-size: 15px; font-weight: bold;">@tns_name</span>
        </div>
        <div>
            <span style="font-size: 10px; color: #696;">Width (ms): </span>
            <span style="font-size: 10px; color: #696;">@width_ms</span>
        </div>
        <hr style="margin: 5px 5px 5px 5px"/>
    </div>
"""

In [7]:
plot = EmbeddingPlot(embeddingFeatureFFT, palette='rainbow', **displayProperties)

plot.run_UMAP(
    n_neighbors=30,
    min_dist=0.1,
    n_components=2,
    metric='euclidean',
    verbose=True
)


UMAP(n_neighbors=30, verbose=True)
Fri Jul  7 16:24:27 2023 Construct fuzzy simplicial set
Fri Jul  7 16:24:27 2023 Finding Nearest Neighbors
Fri Jul  7 16:24:27 2023 Finished Nearest Neighbor Search
Fri Jul  7 16:24:27 2023 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

Fri Jul  7 16:24:33 2023 Finished embedding


In [8]:
plot.make_color_maps(log=True)
plot.show_notebook(
    title='Embedding of FRB 1D Time Series FFT (positive real part) with \n'+str(plot.reducer),
    tools=(
        CopyTool(),
        HoverTool(tooltips=tooltips),
        LassoSelectTool(),
    )
)
plot.save('umap_frb_ts_fft.html')

Loading BokehJS ...

/home/guutz/dawn/dawnplot.py:71: UserWarning: save() called but no resources were supplied and output_file(...) was never called, defaulting to resources.CDN
  bk.save(self.plot, filename)
/home/guutz/dawn/dawnplot.py:71: UserWarning: save() called but no title was supplied and output_file(...) was never called, using default title 'Bokeh Plot'
  bk.save(self.plot, filename)
